In [28]:
!pip install mlflow boto3 awscli optuna imbalanced-learn lightgbm

In [29]:
import mlflow
# Step 2: Set up the MLflow tracking server
mlflow.set_tracking_uri("http://ec2-98-89-47-151.compute-1.amazonaws.com:5000/")

In [30]:
# Set or create an experiment
mlflow.set_experiment("LightGBM HP Tuning")

<Experiment: artifact_location='s3://mlflow-s3-bucket-25/384915840249192182', creation_time=1766406761843, experiment_id='384915840249192182', last_update_time=1766406761843, lifecycle_stage='active', name='LightGBM HP Tuning', tags={}>

In [31]:
import pandas as pd

df = pd.read_csv('reddit_preprocessing.csv').dropna()
df.shape

(36662, 2)

In [32]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from imblearn.over_sampling import SMOTE
import mlflow
import mlflow.sklearn
import optuna
from lightgbm import LGBMClassifier
import matplotlib.pyplot as plt

In [33]:
# Remap the class labels from [-1, 0, 1] to [2, 0, 1]
df['category'] = df['category'].map({-1: 2, 0: 0, 1: 1})

# Remove rows where the target labels (category) are NaN
df = df.dropna(subset=['category'])

In [34]:
# TF-IDF vectorizer setup
ngram_range = (1, 3)  # Trigram
max_features = 1000  # Set max_features to 1000
vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features=max_features)
X = vectorizer.fit_transform(df['clean_comment'])
y = df['category']

# Apply SMOTE to handle class imbalance
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X, y)

In [35]:
# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42, stratify=y_resampled)

In [36]:
# Function to log results in MLflow
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test, params, trial_number):
    with mlflow.start_run():
        # Log model type and trial number
        mlflow.set_tag("mlflow.runName", f"Trial_{trial_number}_{model_name}_SMOTE_TFIDF_Trigrams")
        mlflow.set_tag("experiment_type", "algorithm_comparison")

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)
        
        # Print trial progress
        print(f"Trial {trial_number}: Accuracy = {accuracy:.4f}")

        return accuracy

In [37]:
# Optuna objective function for LightGBM
def objective_lightgbm(trial):
    # Hyperparameter space to explore
    n_estimators = trial.suggest_int('n_estimators', 100, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 15)
    num_leaves = trial.suggest_int('num_leaves', 20, 150)
    min_child_samples = trial.suggest_int('min_child_samples', 10, 100)
    colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0)
    subsample = trial.suggest_float('subsample', 0.5, 1.0)
    reg_alpha = trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True)  # L1 regularization
    reg_lambda = trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True)  # L2 regularization

    # Log trial parameters
    params = {
        'n_estimators': n_estimators,
        'learning_rate': learning_rate,
        'max_depth': max_depth,
        'num_leaves': num_leaves,
        'min_child_samples': min_child_samples,
        'colsample_bytree': colsample_bytree,
        'subsample': subsample,
        'reg_alpha': reg_alpha,
        'reg_lambda': reg_lambda
    }

    # Create LightGBM model
    model = LGBMClassifier(n_estimators=n_estimators,
                           learning_rate=learning_rate,
                           max_depth=max_depth,
                           num_leaves=num_leaves,
                           min_child_samples=min_child_samples,
                           colsample_bytree=colsample_bytree,
                           subsample=subsample,
                           reg_alpha=reg_alpha,
                           reg_lambda=reg_lambda,
                           random_state=42)

    # Log each trial as a separate run in MLflow
    accuracy = log_mlflow("LightGBM", model, X_train, X_test, y_train, y_test, params, trial.number)

    return accuracy

In [38]:
# Run Optuna for LightGBM, log the best model, and plot the importance of each parameter
def run_optuna_experiment():
    print("Starting LightGBM hyperparameter tuning with Optuna...")
    print("Testing 100 different parameter combinations...")
    print("=" * 60)
    
    study = optuna.create_study(direction="maximize")
    study.optimize(objective_lightgbm, n_trials=100, show_progress_bar=True)

    # Get the best parameters
    best_params = study.best_params
    print("\n" + "=" * 60)
    print("Best parameters found:")
    for param, value in best_params.items():
        if isinstance(value, float):
            print(f"  {param}: {value:.6f}")
        else:
            print(f"  {param}: {value}")
    print(f"  Best accuracy: {study.best_value:.4f}")
    print("=" * 60)
    
    # Create the best model with optimal parameters
    best_model = LGBMClassifier(
        n_estimators=best_params['n_estimators'],
        learning_rate=best_params['learning_rate'],
        max_depth=best_params['max_depth'],
        num_leaves=best_params['num_leaves'],
        min_child_samples=best_params['min_child_samples'],
        colsample_bytree=best_params['colsample_bytree'],
        subsample=best_params['subsample'],
        reg_alpha=best_params['reg_alpha'],
        reg_lambda=best_params['reg_lambda'],
        random_state=42
    )
    
    # Log the best model with MLflow
    log_mlflow("LightGBM_Best", best_model, X_train, X_test, y_train, y_test, best_params, "Best")
    
    print("\nYou can view parameter importance in the MLflow UI.")
    print("\nNote: Optuna visualizations are skipped to avoid display issues.")
    print(f"✓ View results: http://ec2-98-89-47-151.compute-1.amazonaws.com:5000/")
    print("\n✓ Experiment completed!")


In [ ]:
# Run the experiment for LightGBM
run_optuna_experiment()

[I 2025-12-22 18:21:03,615] A new study created in memory with name: no-name-03a00232-1bf8-4ead-96b6-d6855954e235


Starting LightGBM hyperparameter tuning with Optuna...
Testing 100 different parameter combinations...


  0%|          | 0/100 [00:00<?, ?it/s]c:\Users\USER\anaconda3\envs\ytsa\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.037896 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 98774
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 956
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

c:\Users\USER\anaconda3\envs\ytsa\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


...

2025/12/22 19:02:47 INFO mlflow.tracking._tracking_service.client: 🏃 View run Trial_45_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-98-89-47-151.compute-1.amazonaws.com:5000/#/experiments/384915840249192182/runs/c590993c44b341b383e60c50ce5271ac.
2025/12/22 19:02:47 INFO mlflow.tracking._tracking_service.client: 🧪 View experiment at: http://ec2-98-89-47-151.compute-1.amazonaws.com:5000/#/experiments/384915840249192182.
Best trial: 32. Best value: 0.822236:  46%|████▌     | 46/100 [41:45<1:10:00, 77.78s/it]

[I 2025-12-22 19:02:49,378] Trial 45 finished with value: 0.820439653350243 and parameters: {'n_estimators': 908, 'learning_rate': 0.06062583199902504, 'max_depth': 13, 'num_leaves': 67, 'min_child_samples': 14, 'colsample_bytree': 0.6107741669875595, 'subsample': 0.9700529373664364, 'reg_alpha': 0.0036371671409054476, 'reg_lambda': 2.0262790284797583}. Best is trial 32 with value: 0.8222363136757557.


c:\Users\USER\anaconda3\envs\ytsa\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.097827 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 99112
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 988
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

c:\Users\USER\anaconda3\envs\ytsa\Lib\site-packages\sklearn\utils\deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
